In [ ]:
!pip install mp-api
!pip install lazypredict
!pip install skipatom
!pip install optuna

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 97.1/97.1 kB 1.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 118.3/118.3 kB 6.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 10.0/10.0 MB 22.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.0/66.0 kB 5.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 198.6/198.6 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 561.4/561.4 kB 32.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.8/117.8 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 670.1/670.1 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.0/60.0 kB 1.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.5/101.5 kB 5.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 91.9/91.9 kB 4.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 920.0/920.0 kB 6.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━

In [ ]:
import pandas as pd
import sklearn
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression, LogisticRegressionCV
from sklearn.ensemble import RandomForestClassifier, RandomForestRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import *
from skipatom import AtomVectors, SkipAtomInducedModel, sum_pool
from pymatgen.core import Composition
import numpy as np
from lazypredict.Supervised import LazyClassifier, LazyRegressor
import optuna
from optuna.samplers import TPESampler
from sklearn.preprocessing import StandardScaler
from numpy import mean
from numpy import std
from pandas import read_csv
from sklearn.model_selection import LeaveOneOut
from sklearn.model_selection import cross_val_score
from sklearn.ensemble import RandomForestClassifier
pd.set_option('display.max_columns', None)

In [ ]:
from google.colab import drive
drive.mount('/content/drive',force_remount=True)

Mounted at /content/drive


In [ ]:
mat2vec_model = AtomVectors.load("/content/drive/MyDrive/mat2vec.dim200.model")
skipatom_model = SkipAtomInducedModel.load("/content/drive/MyDrive/mp_2020_10_09.dim200.model",
                                           "/content/drive/MyDrive/mp_2020_10_09.training.data", min_count=2e7, top_n=5)

In [ ]:
df = pd.read_csv('/content/drive/MyDrive/LiIonDB.csv')
df = df[["Compound","IC"]]
df["ICG"] = (df["IC"]>0.0001).astype(int)
df

Compound   IC  ICG
0          La0.29Li0.12NbO3 0.00    0
1     Li0.8La0.066Zr2(PO4)3 0.00    1
2     Li0.8La0.066Zr2(PO4)3 0.00    1
3     Li0.8La0.066Zr2(PO4)3 0.00    1
4     Li0.8La0.066Zr2(PO4)3 0.00    0
..                      ...  ...  ...
815        Nd0.55Li0.34TiO3 0.00    0
816        Sm0.25Li0.25TaO3 0.00    0
817     Sm0.52Li0.38TiO2.97 0.00    1
818     Sm0.52Li0.38TiO2.97 0.00    0
819         Y0.25Li0.25TaO3 0.00    0

[820 rows x 3 columns]

In [ ]:
df_test=pd.read_csv("/content/drive/MyDrive/test.csv")
df_test = df_test[["Compound","IC"]]
df_test["ICG"] = (df_test["IC"]>0.0001).astype(int)
df_test

Compound   IC  ICG
0             LiLa(TiO3)2 0.00    1
1    Li9.81Sn0.81P2.19S12 0.01    1
2            Li10Ge(PS6)2 0.01    1
3   Li10.35Si1.35P1.65S12 0.01    1
4            Li14ZnGe4O16 0.00    0
5              Li2Ca(NH)2 0.00    0
6               Li2Ge7O15 0.00    0
7                   Li2NH 0.00    1
8                    Li2S 0.00    0
9      Li13.6Si2.8S1.2O16 0.00    0
10           Li14Ge2V2O16 0.00    0
11            Li15Ge3V2O4 0.00    0
12      Li14.8Ge3.4W0.6O4 0.00    0
13            Li3Fe2P3O12 0.00    0
14                   Li3N 0.00    1
15                   Li3P 0.00    1
16                 Li3PS4 0.00    0
17            Li3Sc2P3O12 0.00    0
18                 Li3VO4 0.00    0
19             Li4B7O12Cl 0.00    0
20              Li4BN3H10 0.00    1
21                Li4GeO4 0.00    0
22                Li4SiO4 0.00    0
23           Li5La3Bi2O12 0.00    0
24           Li5La3Nb2O12 0.00    0
25           Li5La3Ta2O12 0.00    0
26                 Li5NI2 0.00    0
27         Li6BaLa2Ta2O12 0.00    0
28               Li6FeCl8 0.00    0
29                Li6NBr3 0.00    0
30         Li6SrLa2Ta2O12 0.00    0
31           Li7La3Zr2O12 0.00    1
32               Li7P3S11 0.00    1
33                 LiAlH4 0.00    0
34               LiAlSiO4 0.00    0
35                  LiBH4 0.00    0
36                    LiI 0.00    0
37                  LiNH2 0.00    0
38             LiZr2P3O12 0.00    0

In [ ]:
#Dropping duplicates and removing common
df=df.drop_duplicates(subset=['Compound'],keep='first').reset_index(drop=True)
df=pd.concat([df,df_test])
df=df.drop_duplicates(subset=['Compound'],keep=False).reset_index(drop=True)
df

Compound   IC  ICG
0                       La0.29Li0.12NbO3 0.00    0
1                  Li0.8La0.066Zr2(PO4)3 0.00    1
2                 Li6.4Al0.19La3Zr2O11.8 0.00    1
3    ((Li2S)0.6 (SiS2)0.4 )95 (Li4SiO4)5 0.04    1
4     ((Li2S)0.6 (SiS2)0.4)95 (Li4SiO4)5 0.00    1
..                                   ...  ...  ...
457                         Li14Ge2V2O16 0.00    0
458                          Li15Ge3V2O4 0.00    0
459                    Li14.8Ge3.4W0.6O4 0.00    0
460                              Li6NBr3 0.00    0
461                                LiNH2 0.00    0

[462 rows x 3 columns]

In [ ]:
def myfunc(x):
  return Composition(x)
df['comp'] = df["Compound"].apply(myfunc)

In [ ]:
df

Compound   IC  ICG                 comp
0                       La0.29Li0.12NbO3 0.00    0      (La, Li, Nb, O)
1                  Li0.8La0.066Zr2(PO4)3 0.00    1   (Li, La, Zr, P, O)
2                 Li6.4Al0.19La3Zr2O11.8 0.00    1  (Li, Al, La, Zr, O)
3    ((Li2S)0.6 (SiS2)0.4 )95 (Li4SiO4)5 0.04    1       (Li, S, Si, O)
4     ((Li2S)0.6 (SiS2)0.4)95 (Li4SiO4)5 0.00    1       (Li, S, Si, O)
..                                   ...  ...  ...                  ...
457                         Li14Ge2V2O16 0.00    0       (Li, Ge, V, O)
458                          Li15Ge3V2O4 0.00    0       (Li, Ge, V, O)
459                    Li14.8Ge3.4W0.6O4 0.00    0       (Li, Ge, W, O)
460                              Li6NBr3 0.00    0          (Li, N, Br)
461                                LiNH2 0.00    0           (Li, N, H)

[462 rows x 4 columns]

In [ ]:
input_vectors = np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df['comp']])

In [ ]:
target_vectors = np.asarray(df['ICG'])

In [ ]:
x_train, x_val, y_train, y_val = train_test_split(input_vectors, target_vectors, random_state=42, stratify=target_vectors,train_size=0.8)

In [ ]:
len(x_train)/(len(x_val)+len(x_train))

0.7987012987012987

In [ ]:
df['ICG'].value_counts()

ICG
0    246
1    216
Name: count, dtype: int64

In [ ]:
clf = LazyClassifier(verbose=None, ignore_warnings=True, custom_metric = None)
m, p = clf.fit(x_train, x_val, y_train, y_val)

 97%|█████████▋| 28/29 [00:06<00:00,  2.56it/s]

[LightGBM] [Info] Number of positive: 173, number of negative: 196
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002434 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 24683
[LightGBM] [Info] Number of data points in the train set: 369, number of used features: 200
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.468835 -> initscore=-0.124823
[LightGBM] [Info] Start training from score -0.124823
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

100%|██████████| 29/29 [00:07<00:00,  4.02it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

In [ ]:
print(p,m)

                               Accuracy  Balanced Accuracy  ROC AUC  F1 Score  \
Model                                                                           
KNeighborsClassifier               0.74               0.74     0.74      0.74   
BaggingClassifier                  0.72               0.72     0.72      0.72   
LabelSpreading                     0.71               0.72     0.72      0.71   
LabelPropagation                   0.71               0.72     0.72      0.71   
NuSVC                              0.72               0.71     0.71      0.72   
RandomForestClassifier             0.70               0.70     0.70      0.70   
LGBMClassifier                     0.69               0.69     0.69      0.69   
LinearSVC                          0.69               0.69     0.69      0.69   
ExtraTreesClassifier               0.68               0.68     0.68      0.68   
BernoulliNB                        0.68               0.66     0.66      0.67   
AdaBoostClassifier          

In [ ]:
def objective(trial):
    n_neighbors = trial.suggest_int("n_neighbors", 1, 50)
    # gamma = trial.suggest_float("gamma", 0.01, 100, log=True)
    # model = sklearn.semi_supervised.LabelPropagation(n_neighbors=n_neighbors, gamma=gamma)
    leaf_size=trial.suggest_int("leaf_size",1,30)
    model = sklearn.neighbors.KNeighborsClassifier(n_neighbors=n_neighbors,leaf_size=leaf_size)
    model.fit(x_train, y_train)
    y_pred = model.predict(x_val)
    return accuracy_score(y_val, y_pred)

In [ ]:
sampler = TPESampler(seed=1)
study = optuna.create_study(direction="maximize", sampler=sampler)
study.optimize(objective, n_trials=500)

print("Number of finished trials: ", len(study.trials))
print("Best trial:")
trial = study.best_trial
print("  Value: ", trial.value)
print("  Params: ")
for key, value in trial.params.items():
    print("    {}: {}".format(key, value))

[I 2024-04-28 13:42:45,145] A new study created in memory with name: no-name-c0d870cb-129b-49ea-b604-c7f824a802f5
[I 2024-04-28 13:42:45,161] Trial 0 finished with value: 0.6129032258064516 and parameters: {'n_neighbors': 21, 'leaf_size': 22}. Best is trial 0 with value: 0.6129032258064516.
[I 2024-04-28 13:42:45,176] Trial 1 finished with value: 0.6666666666666666 and parameters: {'n_neighbors': 1, 'leaf_size': 10}. Best is trial 1 with value: 0.6666666666666666.
[I 2024-04-28 13:42:45,190] Trial 2 finished with value: 0.7096774193548387 and parameters: {'n_neighbors': 8, 'leaf_size': 3}. Best is trial 2 with value: 0.7096774193548387.
[I 2024-04-28 13:42:45,205] Trial 3 finished with value: 0.6989247311827957 and parameters: {'n_neighbors': 10, 'leaf_size': 11}. Best is trial 2 with value: 0.7096774193548387.
[I 2024-04-28 13:42:45,222] Trial 4 finished with value: 0.6236559139784946 and parameters: {'n_neighbors': 20, 'leaf_size': 17}. Best is trial 2 with value: 0.7096774193548387.

Number of finished trials:  500
Best trial:
  Value:  0.7634408602150538
  Params: 
    n_neighbors: 2
    leaf_size: 21


In [ ]:
# model = sklearn.ensemble.AdaBoostClassifier()
# model=sklearn.ensemble.RandomForestClassifier()
# model=sklearn.semi_supervised.LabelPropagation(n_neighbors=trial.params['n_neighbors'],gamma=trial.params['gamma'])
model=sklearn.neighbors.KNeighborsClassifier(n_neighbors=trial.params['n_neighbors'],leaf_size=trial.params['leaf_size'])
model.fit(x_train,y_train)

KNeighborsClassifier(leaf_size=21, n_neighbors=2)

In [ ]:
pred_train=model.predict(x_train)
pred_val=model.predict(x_val)
print(classification_report(y_train,pred_train))
print(f1_score(y_train, pred_train))
print(classification_report(y_val,pred_val))
print(f1_score(y_val, pred_val))

              precision    recall  f1-score   support

           0       0.84      1.00      0.91       196
           1       1.00      0.79      0.88       173

    accuracy                           0.90       369
   macro avg       0.92      0.89      0.90       369
weighted avg       0.92      0.90      0.90       369

0.8802588996763754
              precision    recall  f1-score   support

           0       0.74      0.86      0.80        50
           1       0.80      0.65      0.72        43

    accuracy                           0.76        93
   macro avg       0.77      0.76      0.76        93
weighted avg       0.77      0.76      0.76        93

0.7179487179487181


In [ ]:
df_test

Compound   IC  ICG
0             LiLa(TiO3)2 0.00    1
1    Li9.81Sn0.81P2.19S12 0.01    1
2            Li10Ge(PS6)2 0.01    1
3   Li10.35Si1.35P1.65S12 0.01    1
4            Li14ZnGe4O16 0.00    0
5              Li2Ca(NH)2 0.00    0
6               Li2Ge7O15 0.00    0
7                   Li2NH 0.00    1
8                    Li2S 0.00    0
9      Li13.6Si2.8S1.2O16 0.00    0
10           Li14Ge2V2O16 0.00    0
11            Li15Ge3V2O4 0.00    0
12      Li14.8Ge3.4W0.6O4 0.00    0
13            Li3Fe2P3O12 0.00    0
14                   Li3N 0.00    1
15                   Li3P 0.00    1
16                 Li3PS4 0.00    0
17            Li3Sc2P3O12 0.00    0
18                 Li3VO4 0.00    0
19             Li4B7O12Cl 0.00    0
20              Li4BN3H10 0.00    1
21                Li4GeO4 0.00    0
22                Li4SiO4 0.00    0
23           Li5La3Bi2O12 0.00    0
24           Li5La3Nb2O12 0.00    0
25           Li5La3Ta2O12 0.00    0
26                 Li5NI2 0.00    0
27         Li6BaLa2Ta2O12 0.00    0
28               Li6FeCl8 0.00    0
29                Li6NBr3 0.00    0
30         Li6SrLa2Ta2O12 0.00    0
31           Li7La3Zr2O12 0.00    1
32               Li7P3S11 0.00    1
33                 LiAlH4 0.00    0
34               LiAlSiO4 0.00    0
35                  LiBH4 0.00    0
36                    LiI 0.00    0
37                  LiNH2 0.00    0
38             LiZr2P3O12 0.00    0

In [ ]:
df_test['ICG'].value_counts()

ICG
0    29
1    10
Name: count, dtype: int64

In [ ]:
df_test["comp"]=df_test["Compound"].apply(myfunc)

In [ ]:
df_test

Compound   IC  ICG                 comp
0             LiLa(TiO3)2 0.00    1      (Li, La, Ti, O)
1    Li9.81Sn0.81P2.19S12 0.01    1       (Li, Sn, P, S)
2            Li10Ge(PS6)2 0.01    1       (Li, Ge, P, S)
3   Li10.35Si1.35P1.65S12 0.01    1       (Li, Si, P, S)
4            Li14ZnGe4O16 0.00    0      (Li, Zn, Ge, O)
5              Li2Ca(NH)2 0.00    0       (Li, Ca, N, H)
6               Li2Ge7O15 0.00    0          (Li, Ge, O)
7                   Li2NH 0.00    1           (Li, N, H)
8                    Li2S 0.00    0              (Li, S)
9      Li13.6Si2.8S1.2O16 0.00    0       (Li, Si, S, O)
10           Li14Ge2V2O16 0.00    0       (Li, Ge, V, O)
11            Li15Ge3V2O4 0.00    0       (Li, Ge, V, O)
12      Li14.8Ge3.4W0.6O4 0.00    0       (Li, Ge, W, O)
13            Li3Fe2P3O12 0.00    0       (Li, Fe, P, O)
14                   Li3N 0.00    1              (Li, N)
15                   Li3P 0.00    1              (Li, P)
16                 Li3PS4 0.00    0           (Li, P, S)
17            Li3Sc2P3O12 0.00    0       (Li, Sc, P, O)
18                 Li3VO4 0.00    0           (Li, V, O)
19             Li4B7O12Cl 0.00    0       (Li, B, O, Cl)
20              Li4BN3H10 0.00    1        (Li, B, N, H)
21                Li4GeO4 0.00    0          (Li, Ge, O)
22                Li4SiO4 0.00    0          (Li, Si, O)
23           Li5La3Bi2O12 0.00    0      (Li, La, Bi, O)
24           Li5La3Nb2O12 0.00    0      (Li, La, Nb, O)
25           Li5La3Ta2O12 0.00    0      (Li, La, Ta, O)
26                 Li5NI2 0.00    0           (Li, N, I)
27         Li6BaLa2Ta2O12 0.00    0  (Li, Ba, La, Ta, O)
28               Li6FeCl8 0.00    0         (Li, Fe, Cl)
29                Li6NBr3 0.00    0          (Li, N, Br)
30         Li6SrLa2Ta2O12 0.00    0  (Li, Sr, La, Ta, O)
31           Li7La3Zr2O12 0.00    1      (Li, La, Zr, O)
32               Li7P3S11 0.00    1           (Li, P, S)
33                 LiAlH4 0.00    0          (Li, Al, H)
34               LiAlSiO4 0.00    0      (Li, Al, Si, O)
35                  LiBH4 0.00    0           (Li, B, H)
36                    LiI 0.00    0              (Li, I)
37                  LiNH2 0.00    0           (Li, N, H)
38             LiZr2P3O12 0.00    0       (Li, Zr, P, O)

In [ ]:
x_test= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_test['comp']])
y_test= np.asarray(df_test['ICG'])

In [ ]:
x_test

array([[-0.07437761, -1.90261572,  0.32049516, ...,  3.05274728,
        -0.61296411,  0.65849499],
       [ 2.13703611, -0.15460631,  1.7088802 , ...,  8.50393609,
         1.29005215,  4.29436217],
       [ 2.31542532, -0.06324767,  1.65262189, ...,  8.3133341 ,
         1.33158444,  4.36008996],
       ...,
       [-0.10946507,  0.18374575, -0.02907139, ..., -0.02786765,
         0.16179648,  0.54381947],
       [-0.06036078, -0.3762809 ,  0.68075192, ...,  1.19470659,
         0.42982607,  0.05445369],
       [-1.3245857 , -3.22449232,  1.06921921, ...,  4.23231442,
        -1.37074712,  0.26337109]])

In [ ]:
pred_test=model.predict(x_test)

In [ ]:
pred_test

array([0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0,
       1, 0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 0, 0, 0, 0, 0])

In [ ]:
pred_test=model.predict(x_test)
print(classification_report(y_test,pred_test))

              precision    recall  f1-score   support

           0       0.81      0.86      0.83        29
           1       0.50      0.40      0.44        10

    accuracy                           0.74        39
   macro avg       0.65      0.63      0.64        39
weighted avg       0.73      0.74      0.73        39



In [ ]:
f1_score(y_test, pred_test)

0.4444444444444445

In [ ]:
f1_score(y_test, pred_test, average="macro")

0.638888888888889

In [ ]:
f1_score(y_test, pred_test, average="micro")

0.7435897435897437

In [ ]:
f1_score(y_test, pred_test, average="weighted")

0.7336182336182338

In [ ]:
df_test["preds"]=pred_test

In [ ]:
df_test

Compound   IC  ICG                 comp  preds
0             LiLa(TiO3)2 0.00    1      (Li, La, Ti, O)      0
1    Li9.81Sn0.81P2.19S12 0.01    1       (Li, Sn, P, S)      1
2            Li10Ge(PS6)2 0.01    1       (Li, Ge, P, S)      1
3   Li10.35Si1.35P1.65S12 0.01    1       (Li, Si, P, S)      1
4            Li14ZnGe4O16 0.00    0      (Li, Zn, Ge, O)      0
5              Li2Ca(NH)2 0.00    0       (Li, Ca, N, H)      0
6               Li2Ge7O15 0.00    0          (Li, Ge, O)      0
7                   Li2NH 0.00    1           (Li, N, H)      0
8                    Li2S 0.00    0              (Li, S)      0
9      Li13.6Si2.8S1.2O16 0.00    0       (Li, Si, S, O)      0
10           Li14Ge2V2O16 0.00    0       (Li, Ge, V, O)      0
11            Li15Ge3V2O4 0.00    0       (Li, Ge, V, O)      0
12      Li14.8Ge3.4W0.6O4 0.00    0       (Li, Ge, W, O)      0
13            Li3Fe2P3O12 0.00    0       (Li, Fe, P, O)      0
14                   Li3N 0.00    1              (Li, N)      0
15                   Li3P 0.00    1              (Li, P)      0
16                 Li3PS4 0.00    0           (Li, P, S)      1
17            Li3Sc2P3O12 0.00    0       (Li, Sc, P, O)      0
18                 Li3VO4 0.00    0           (Li, V, O)      0
19             Li4B7O12Cl 0.00    0       (Li, B, O, Cl)      0
20              Li4BN3H10 0.00    1        (Li, B, N, H)      0
21                Li4GeO4 0.00    0          (Li, Ge, O)      0
22                Li4SiO4 0.00    0          (Li, Si, O)      1
23           Li5La3Bi2O12 0.00    0      (Li, La, Bi, O)      0
24           Li5La3Nb2O12 0.00    0      (Li, La, Nb, O)      0
25           Li5La3Ta2O12 0.00    0      (Li, La, Ta, O)      0
26                 Li5NI2 0.00    0           (Li, N, I)      0
27         Li6BaLa2Ta2O12 0.00    0  (Li, Ba, La, Ta, O)      1
28               Li6FeCl8 0.00    0         (Li, Fe, Cl)      0
29                Li6NBr3 0.00    0          (Li, N, Br)      0
30         Li6SrLa2Ta2O12 0.00    0  (Li, Sr, La, Ta, O)      1
31           Li7La3Zr2O12 0.00    1      (Li, La, Zr, O)      0
32               Li7P3S11 0.00    1           (Li, P, S)      1
33                 LiAlH4 0.00    0          (Li, Al, H)      0
34               LiAlSiO4 0.00    0      (Li, Al, Si, O)      0
35                  LiBH4 0.00    0           (Li, B, H)      0
36                    LiI 0.00    0              (Li, I)      0
37                  LiNH2 0.00    0           (Li, N, H)      0
38             LiZr2P3O12 0.00    0       (Li, Zr, P, O)      0

In [ ]:
df_label=pd.read_csv("/content/drive/MyDrive/test_elem_new.csv")
df_label["comp"]=df_label["Compounds"].apply(myfunc)
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_label['comp']])
pred_test=model.predict(x_label)
df_label["preds"]=pred_test
df_label.to_excel("predictions_allT.xlsx")

#At Room Temperature

In [ ]:
df = pd.read_csv('/content/drive/MyDrive/LiIonDB.csv')
df = df[(df['T'] >= 22.0) & (df['T'] <= 26.0)].reset_index(drop=True)
df = df[["Compound","IC"]]
df["ICG"] = (df["IC"]>0.0001).astype(int)
df

Compound   IC  ICG
0                       La0.29Li0.12NbO3 0.00    0
1                  Li0.8La0.066Zr2(PO4)3 0.00    0
2                 Li6.4Al0.19La3Zr2O11.8 0.00    1
3    ((Li2S)0.6 (SiS2)0.4 )95 (Li4SiO4)5 0.01    1
4                  (Li2O)16.6 (SiO2)83.4 0.00    0
..                                   ...  ...  ...
348                          LiZr2(PO4)3 0.00    0
349                          LiZr2(PO4)3 0.00    0
350                     Nd0.25Li0.25TaO3 0.00    0
351                     Nd0.55Li0.34TiO3 0.00    0
352                  Sm0.52Li0.38TiO2.97 0.00    1

[353 rows x 3 columns]

In [ ]:
df_test=pd.read_csv("/content/drive/MyDrive/test.csv")
df_test = df_test[["Compound","IC"]]
df_test["ICG"] = (df_test["IC"]>0.0001).astype(int)
df_test

Compound   IC  ICG
0             LiLa(TiO3)2 0.00    1
1    Li9.81Sn0.81P2.19S12 0.01    1
2            Li10Ge(PS6)2 0.01    1
3   Li10.35Si1.35P1.65S12 0.01    1
4            Li14ZnGe4O16 0.00    0
5              Li2Ca(NH)2 0.00    0
6               Li2Ge7O15 0.00    0
7                   Li2NH 0.00    1
8                    Li2S 0.00    0
9      Li13.6Si2.8S1.2O16 0.00    0
10           Li14Ge2V2O16 0.00    0
11            Li15Ge3V2O4 0.00    0
12      Li14.8Ge3.4W0.6O4 0.00    0
13            Li3Fe2P3O12 0.00    0
14                   Li3N 0.00    1
15                   Li3P 0.00    1
16                 Li3PS4 0.00    0
17            Li3Sc2P3O12 0.00    0
18                 Li3VO4 0.00    0
19             Li4B7O12Cl 0.00    0
20              Li4BN3H10 0.00    1
21                Li4GeO4 0.00    0
22                Li4SiO4 0.00    0
23           Li5La3Bi2O12 0.00    0
24           Li5La3Nb2O12 0.00    0
25           Li5La3Ta2O12 0.00    0
26                 Li5NI2 0.00    0
27         Li6BaLa2Ta2O12 0.00    0
28               Li6FeCl8 0.00    0
29                Li6NBr3 0.00    0
30         Li6SrLa2Ta2O12 0.00    0
31           Li7La3Zr2O12 0.00    1
32               Li7P3S11 0.00    1
33                 LiAlH4 0.00    0
34               LiAlSiO4 0.00    0
35                  LiBH4 0.00    0
36                    LiI 0.00    0
37                  LiNH2 0.00    0
38             LiZr2P3O12 0.00    0

In [ ]:
#Dropping duplicates and removing common
df=df.drop_duplicates(subset=['Compound'],keep='first').reset_index(drop=True)
df=pd.concat([df,df_test])
df=df.drop_duplicates(subset=['Compound'],keep=False).reset_index(drop=True)
df

Compound   IC  ICG
0                       La0.29Li0.12NbO3 0.00    0
1                  Li0.8La0.066Zr2(PO4)3 0.00    0
2                 Li6.4Al0.19La3Zr2O11.8 0.00    1
3    ((Li2S)0.6 (SiS2)0.4 )95 (Li4SiO4)5 0.01    1
4                  (Li2O)16.6 (SiO2)83.4 0.00    0
..                                   ...  ...  ...
309                              Li6NBr3 0.00    0
310                             LiAlSiO4 0.00    0
311                                LiBH4 0.00    0
312                                LiNH2 0.00    0
313                           LiZr2P3O12 0.00    0

[314 rows x 3 columns]

In [ ]:
def myfunc(x):
  return Composition(x)
df['comp'] = df["Compound"].apply(myfunc)

In [ ]:
df

Compound   IC  ICG                 comp
0                       La0.29Li0.12NbO3 0.00    0      (La, Li, Nb, O)
1                  Li0.8La0.066Zr2(PO4)3 0.00    0   (Li, La, Zr, P, O)
2                 Li6.4Al0.19La3Zr2O11.8 0.00    1  (Li, Al, La, Zr, O)
3    ((Li2S)0.6 (SiS2)0.4 )95 (Li4SiO4)5 0.01    1       (Li, S, Si, O)
4                  (Li2O)16.6 (SiO2)83.4 0.00    0          (Li, O, Si)
..                                   ...  ...  ...                  ...
309                              Li6NBr3 0.00    0          (Li, N, Br)
310                             LiAlSiO4 0.00    0      (Li, Al, Si, O)
311                                LiBH4 0.00    0           (Li, B, H)
312                                LiNH2 0.00    0           (Li, N, H)
313                           LiZr2P3O12 0.00    0       (Li, Zr, P, O)

[314 rows x 4 columns]

In [ ]:
input_vectors = np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df['comp']])

In [ ]:
target_vectors = np.asarray(df['ICG'])

In [ ]:
x_train, x_val, y_train, y_val = train_test_split(input_vectors, target_vectors, random_state=42, stratify=target_vectors,train_size=0.8)

In [ ]:
len(x_train)/(len(x_val)+len(x_train))

0.7993630573248408

In [ ]:
df['ICG'].value_counts()

ICG
0    187
1    127
Name: count, dtype: int64

In [ ]:
clf = LazyClassifier(verbose=None, ignore_warnings=True, custom_metric = None)
m, p = clf.fit(x_train, x_val, y_train, y_val)

 97%|█████████▋| 28/29 [00:05<00:00,  4.17it/s]

[LightGBM] [Info] Number of positive: 102, number of negative: 149
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001341 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 16903
[LightGBM] [Info] Number of data points in the train set: 251, number of used features: 200
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.406375 -> initscore=-0.378973
[LightGBM] [Info] Start training from score -0.378973
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

100%|██████████| 29/29 [00:05<00:00,  5.31it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

In [ ]:
print(p,m)

                               Accuracy  Balanced Accuracy  ROC AUC  F1 Score  \
Model                                                                           
LGBMClassifier                     0.86               0.85     0.85      0.86   
ExtraTreesClassifier               0.84               0.81     0.81      0.83   
LabelPropagation                   0.79               0.79     0.79      0.80   
KNeighborsClassifier               0.79               0.79     0.79      0.79   
AdaBoostClassifier                 0.79               0.78     0.78      0.79   
LabelSpreading                     0.78               0.77     0.77      0.78   
RandomForestClassifier             0.79               0.77     0.77      0.79   
XGBClassifier                      0.78               0.76     0.76      0.78   
RidgeClassifierCV                  0.76               0.75     0.75      0.76   
DecisionTreeClassifier             0.75               0.73     0.73      0.75   
LogisticRegression          

In [ ]:
import lightgbm as lgb

def objective(trial):
    num_leaves = trial.suggest_int("num_leaves", 20, 120)
    boosting_type = trial.suggest_categorical("boosting_type", ["gbdt","dart"])
    model = lgb.LGBMClassifier(boosting_type=boosting_type,num_leaves=num_leaves,random_state=42)
    model.fit(x_train, y_train)
    y_pred = model.predict(x_val)
    return accuracy_score(y_val, y_pred)

In [ ]:
sampler = TPESampler(seed=1)
study = optuna.create_study(direction="maximize", sampler=sampler)
study.optimize(objective, n_trials=500)

print("Number of finished trials: ", len(study.trials))
print("Best trial:")
trial = study.best_trial
print("  Value: ", trial.value)
print("  Params: ")
for key, value in trial.params.items():
    print("    {}: {}".format(key, value))

[I 2024-04-28 13:43:13,264] A new study created in memory with name: no-name-9bafd06b-43ee-4794-8af2-a8b807c11589


[LightGBM] [Info] Number of positive: 102, number of negative: 149
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000968 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 16883
[LightGBM] [Info] Number of data points in the train set: 251, number of used features: 200
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.406375 -> initscore=-0.378973
[LightGBM] [Info] Start training from score -0.378973
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

[I 2024-04-28 13:43:13,537] Trial 0 finished with value: 0.8412698412698413 and parameters: {'num_leaves': 62, 'boosting_type': 'gbdt'}. Best is trial 0 with value: 0.8412698412698413.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-04-28 13:43:13,792] Trial 1 finished with value: 0.8412698412698413 and parameters: {'num_leaves': 50, 'boosting_type': 'gbdt'}. Best is trial 0 with value: 0.8412698412698413.


...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-04-28 13:46:22,496] Trial 498 finished with value: 0.8412698412698413 and parameters: {'num_leaves': 73, 'boosting_type': 'gbdt'}. Best is trial 0 with value: 0.8412698412698413.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

[I 2024-04-28 13:46:22,871] Trial 499 finished with value: 0.8412698412698413 and parameters: {'num_leaves': 48, 'boosting_type': 'gbdt'}. Best is trial 0 with value: 0.8412698412698413.


[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

In [ ]:
# model = sklearn.ensemble.AdaBoostClassifier()
# model=sklearn.ensemble.RandomForestClassifier()
# model=sklearn.semi_supervised.LabelPropagation(n_neighbors=trial.params['n_neighbors'],gamma=trial.params['gamma'])
# model = sklearn.svm.LinearSVC(C=trial.params['C'],random_state=42)
model = lgb.LGBMClassifier(boosting_type=trial.params['boosting_type'],num_leaves=trial.params['num_leaves'],random_state=42)
model.fit(x_train,y_train)

[LightGBM] [Info] Number of positive: 102, number of negative: 149
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001374 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 16883
[LightGBM] [Info] Number of data points in the train set: 251, number of used features: 200
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.406375 -> initscore=-0.378973
[LightGBM] [Info] Start training from score -0.378973
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, b

LGBMClassifier(num_leaves=62, random_state=42)

In [ ]:
pred_train=model.predict(x_train)
pred_val=model.predict(x_val)
print(classification_report(y_train,pred_train))
print(f1_score(y_train, pred_train))
print(classification_report(y_val,pred_val))
print(f1_score(y_val, pred_val))

              precision    recall  f1-score   support

           0       1.00      1.00      1.00       149
           1       1.00      1.00      1.00       102

    accuracy                           1.00       251
   macro avg       1.00      1.00      1.00       251
weighted avg       1.00      1.00      1.00       251

1.0
              precision    recall  f1-score   support

           0       0.85      0.89      0.87        38
           1       0.83      0.76      0.79        25

    accuracy                           0.84        63
   macro avg       0.84      0.83      0.83        63
weighted avg       0.84      0.84      0.84        63

0.7916666666666667


In [ ]:
df_test

Compound   IC  ICG
0             LiLa(TiO3)2 0.00    1
1    Li9.81Sn0.81P2.19S12 0.01    1
2            Li10Ge(PS6)2 0.01    1
3   Li10.35Si1.35P1.65S12 0.01    1
4            Li14ZnGe4O16 0.00    0
5              Li2Ca(NH)2 0.00    0
6               Li2Ge7O15 0.00    0
7                   Li2NH 0.00    1
8                    Li2S 0.00    0
9      Li13.6Si2.8S1.2O16 0.00    0
10           Li14Ge2V2O16 0.00    0
11            Li15Ge3V2O4 0.00    0
12      Li14.8Ge3.4W0.6O4 0.00    0
13            Li3Fe2P3O12 0.00    0
14                   Li3N 0.00    1
15                   Li3P 0.00    1
16                 Li3PS4 0.00    0
17            Li3Sc2P3O12 0.00    0
18                 Li3VO4 0.00    0
19             Li4B7O12Cl 0.00    0
20              Li4BN3H10 0.00    1
21                Li4GeO4 0.00    0
22                Li4SiO4 0.00    0
23           Li5La3Bi2O12 0.00    0
24           Li5La3Nb2O12 0.00    0
25           Li5La3Ta2O12 0.00    0
26                 Li5NI2 0.00    0
27         Li6BaLa2Ta2O12 0.00    0
28               Li6FeCl8 0.00    0
29                Li6NBr3 0.00    0
30         Li6SrLa2Ta2O12 0.00    0
31           Li7La3Zr2O12 0.00    1
32               Li7P3S11 0.00    1
33                 LiAlH4 0.00    0
34               LiAlSiO4 0.00    0
35                  LiBH4 0.00    0
36                    LiI 0.00    0
37                  LiNH2 0.00    0
38             LiZr2P3O12 0.00    0

In [ ]:
df_test['ICG'].value_counts()

ICG
0    29
1    10
Name: count, dtype: int64

In [ ]:
df_test["comp"]=df_test["Compound"].apply(myfunc)

In [ ]:
df_test

Compound   IC  ICG                 comp
0             LiLa(TiO3)2 0.00    1      (Li, La, Ti, O)
1    Li9.81Sn0.81P2.19S12 0.01    1       (Li, Sn, P, S)
2            Li10Ge(PS6)2 0.01    1       (Li, Ge, P, S)
3   Li10.35Si1.35P1.65S12 0.01    1       (Li, Si, P, S)
4            Li14ZnGe4O16 0.00    0      (Li, Zn, Ge, O)
5              Li2Ca(NH)2 0.00    0       (Li, Ca, N, H)
6               Li2Ge7O15 0.00    0          (Li, Ge, O)
7                   Li2NH 0.00    1           (Li, N, H)
8                    Li2S 0.00    0              (Li, S)
9      Li13.6Si2.8S1.2O16 0.00    0       (Li, Si, S, O)
10           Li14Ge2V2O16 0.00    0       (Li, Ge, V, O)
11            Li15Ge3V2O4 0.00    0       (Li, Ge, V, O)
12      Li14.8Ge3.4W0.6O4 0.00    0       (Li, Ge, W, O)
13            Li3Fe2P3O12 0.00    0       (Li, Fe, P, O)
14                   Li3N 0.00    1              (Li, N)
15                   Li3P 0.00    1              (Li, P)
16                 Li3PS4 0.00    0           (Li, P, S)
17            Li3Sc2P3O12 0.00    0       (Li, Sc, P, O)
18                 Li3VO4 0.00    0           (Li, V, O)
19             Li4B7O12Cl 0.00    0       (Li, B, O, Cl)
20              Li4BN3H10 0.00    1        (Li, B, N, H)
21                Li4GeO4 0.00    0          (Li, Ge, O)
22                Li4SiO4 0.00    0          (Li, Si, O)
23           Li5La3Bi2O12 0.00    0      (Li, La, Bi, O)
24           Li5La3Nb2O12 0.00    0      (Li, La, Nb, O)
25           Li5La3Ta2O12 0.00    0      (Li, La, Ta, O)
26                 Li5NI2 0.00    0           (Li, N, I)
27         Li6BaLa2Ta2O12 0.00    0  (Li, Ba, La, Ta, O)
28               Li6FeCl8 0.00    0         (Li, Fe, Cl)
29                Li6NBr3 0.00    0          (Li, N, Br)
30         Li6SrLa2Ta2O12 0.00    0  (Li, Sr, La, Ta, O)
31           Li7La3Zr2O12 0.00    1      (Li, La, Zr, O)
32               Li7P3S11 0.00    1           (Li, P, S)
33                 LiAlH4 0.00    0          (Li, Al, H)
34               LiAlSiO4 0.00    0      (Li, Al, Si, O)
35                  LiBH4 0.00    0           (Li, B, H)
36                    LiI 0.00    0              (Li, I)
37                  LiNH2 0.00    0           (Li, N, H)
38             LiZr2P3O12 0.00    0       (Li, Zr, P, O)

In [ ]:
x_test= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_test['comp']])
y_test= np.asarray(df_test['ICG'])

In [ ]:
x_test

array([[-0.07437761, -1.90261572,  0.32049516, ...,  3.05274728,
        -0.61296411,  0.65849499],
       [ 2.13703611, -0.15460631,  1.7088802 , ...,  8.50393609,
         1.29005215,  4.29436217],
       [ 2.31542532, -0.06324767,  1.65262189, ...,  8.3133341 ,
         1.33158444,  4.36008996],
       ...,
       [-0.10946507,  0.18374575, -0.02907139, ..., -0.02786765,
         0.16179648,  0.54381947],
       [-0.06036078, -0.3762809 ,  0.68075192, ...,  1.19470659,
         0.42982607,  0.05445369],
       [-1.3245857 , -3.22449232,  1.06921921, ...,  4.23231442,
        -1.37074712,  0.26337109]])

In [ ]:
pred_test=model.predict(x_test)

In [ ]:
pred_test

array([0, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0,
       0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0, 0, 0, 1, 0, 0])

In [ ]:
pred_test=model.predict(x_test)
print(classification_report(y_test,pred_test))

              precision    recall  f1-score   support

           0       0.87      0.93      0.90        29
           1       0.75      0.60      0.67        10

    accuracy                           0.85        39
   macro avg       0.81      0.77      0.78        39
weighted avg       0.84      0.85      0.84        39



In [ ]:
df_test["preds"]=pred_test

In [ ]:
df_test

Compound   IC  ICG                 comp  preds
0             LiLa(TiO3)2 0.00    1      (Li, La, Ti, O)      0
1    Li9.81Sn0.81P2.19S12 0.01    1       (Li, Sn, P, S)      1
2            Li10Ge(PS6)2 0.01    1       (Li, Ge, P, S)      1
3   Li10.35Si1.35P1.65S12 0.01    1       (Li, Si, P, S)      1
4            Li14ZnGe4O16 0.00    0      (Li, Zn, Ge, O)      0
5              Li2Ca(NH)2 0.00    0       (Li, Ca, N, H)      0
6               Li2Ge7O15 0.00    0          (Li, Ge, O)      0
7                   Li2NH 0.00    1           (Li, N, H)      0
8                    Li2S 0.00    0              (Li, S)      0
9      Li13.6Si2.8S1.2O16 0.00    0       (Li, Si, S, O)      0
10           Li14Ge2V2O16 0.00    0       (Li, Ge, V, O)      0
11            Li15Ge3V2O4 0.00    0       (Li, Ge, V, O)      0
12      Li14.8Ge3.4W0.6O4 0.00    0       (Li, Ge, W, O)      0
13            Li3Fe2P3O12 0.00    0       (Li, Fe, P, O)      0
14                   Li3N 0.00    1              (Li, N)      0
15                   Li3P 0.00    1              (Li, P)      0
16                 Li3PS4 0.00    0           (Li, P, S)      1
17            Li3Sc2P3O12 0.00    0       (Li, Sc, P, O)      0
18                 Li3VO4 0.00    0           (Li, V, O)      0
19             Li4B7O12Cl 0.00    0       (Li, B, O, Cl)      0
20              Li4BN3H10 0.00    1        (Li, B, N, H)      1
21                Li4GeO4 0.00    0          (Li, Ge, O)      0
22                Li4SiO4 0.00    0          (Li, Si, O)      0
23           Li5La3Bi2O12 0.00    0      (Li, La, Bi, O)      0
24           Li5La3Nb2O12 0.00    0      (Li, La, Nb, O)      0
25           Li5La3Ta2O12 0.00    0      (Li, La, Ta, O)      0
26                 Li5NI2 0.00    0           (Li, N, I)      0
27         Li6BaLa2Ta2O12 0.00    0  (Li, Ba, La, Ta, O)      0
28               Li6FeCl8 0.00    0         (Li, Fe, Cl)      0
29                Li6NBr3 0.00    0          (Li, N, Br)      0
30         Li6SrLa2Ta2O12 0.00    0  (Li, Sr, La, Ta, O)      0
31           Li7La3Zr2O12 0.00    1      (Li, La, Zr, O)      1
32               Li7P3S11 0.00    1           (Li, P, S)      1
33                 LiAlH4 0.00    0          (Li, Al, H)      0
34               LiAlSiO4 0.00    0      (Li, Al, Si, O)      0
35                  LiBH4 0.00    0           (Li, B, H)      0
36                    LiI 0.00    0              (Li, I)      1
37                  LiNH2 0.00    0           (Li, N, H)      0
38             LiZr2P3O12 0.00    0       (Li, Zr, P, O)      0

In [ ]:
df_label=pd.read_csv("/content/drive/MyDrive/test_elem_new.csv")
df_label["comp"]=df_label["Compounds"].apply(myfunc)
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_label['comp']])
pred_test=model.predict(x_label)
df_label["preds"]=pred_test
df_label.to_excel("predictions_RoomT.xlsx")

#Final Testing

EXP DATASET (LOOCV)

In [ ]:
df_test

Compound   IC  ICG                 comp  preds
0             LiLa(TiO3)2 0.00    1      (Li, La, Ti, O)      0
1    Li9.81Sn0.81P2.19S12 0.01    1       (Li, Sn, P, S)      1
2            Li10Ge(PS6)2 0.01    1       (Li, Ge, P, S)      1
3   Li10.35Si1.35P1.65S12 0.01    1       (Li, Si, P, S)      1
4            Li14ZnGe4O16 0.00    0      (Li, Zn, Ge, O)      0
5              Li2Ca(NH)2 0.00    0       (Li, Ca, N, H)      0
6               Li2Ge7O15 0.00    0          (Li, Ge, O)      0
7                   Li2NH 0.00    1           (Li, N, H)      0
8                    Li2S 0.00    0              (Li, S)      0
9      Li13.6Si2.8S1.2O16 0.00    0       (Li, Si, S, O)      0
10           Li14Ge2V2O16 0.00    0       (Li, Ge, V, O)      0
11            Li15Ge3V2O4 0.00    0       (Li, Ge, V, O)      0
12      Li14.8Ge3.4W0.6O4 0.00    0       (Li, Ge, W, O)      0
13            Li3Fe2P3O12 0.00    0       (Li, Fe, P, O)      0
14                   Li3N 0.00    1              (Li, N)      0
15                   Li3P 0.00    1              (Li, P)      0
16                 Li3PS4 0.00    0           (Li, P, S)      1
17            Li3Sc2P3O12 0.00    0       (Li, Sc, P, O)      0
18                 Li3VO4 0.00    0           (Li, V, O)      0
19             Li4B7O12Cl 0.00    0       (Li, B, O, Cl)      0
20              Li4BN3H10 0.00    1        (Li, B, N, H)      1
21                Li4GeO4 0.00    0          (Li, Ge, O)      0
22                Li4SiO4 0.00    0          (Li, Si, O)      0
23           Li5La3Bi2O12 0.00    0      (Li, La, Bi, O)      0
24           Li5La3Nb2O12 0.00    0      (Li, La, Nb, O)      0
25           Li5La3Ta2O12 0.00    0      (Li, La, Ta, O)      0
26                 Li5NI2 0.00    0           (Li, N, I)      0
27         Li6BaLa2Ta2O12 0.00    0  (Li, Ba, La, Ta, O)      0
28               Li6FeCl8 0.00    0         (Li, Fe, Cl)      0
29                Li6NBr3 0.00    0          (Li, N, Br)      0
30         Li6SrLa2Ta2O12 0.00    0  (Li, Sr, La, Ta, O)      0
31           Li7La3Zr2O12 0.00    1      (Li, La, Zr, O)      1
32               Li7P3S11 0.00    1           (Li, P, S)      1
33                 LiAlH4 0.00    0          (Li, Al, H)      0
34               LiAlSiO4 0.00    0      (Li, Al, Si, O)      0
35                  LiBH4 0.00    0           (Li, B, H)      0
36                    LiI 0.00    0              (Li, I)      1
37                  LiNH2 0.00    0           (Li, N, H)      0
38             LiZr2P3O12 0.00    0       (Li, Zr, P, O)      0

In [ ]:
df_results=df_test
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_results['comp']])
pred_test=model.predict(x_label)
y_label= np.asarray(df_results["ICG"])

In [ ]:
print(classification_report(y_label,pred_test))

              precision    recall  f1-score   support

           0       0.87      0.93      0.90        29
           1       0.75      0.60      0.67        10

    accuracy                           0.85        39
   macro avg       0.81      0.77      0.78        39
weighted avg       0.84      0.85      0.84        39



In [ ]:
# X, y = x_label,y_label
# # print(X.shape, y.shape)
# # create loocv procedure
# cv = LeaveOneOut()
# # create model
# model1 = sklearn.svm.LinearSVC(C=trial.params['C'],random_state=42)
# # evaluate model
# scores = cross_val_score(model1, X, y, scoring='accuracy', cv=cv, n_jobs=-1)
# # report performance
# print('Accuracy: %.3f (STD: %.3f)' % (mean(scores), std(scores)))

MP DATASET

In [ ]:
df_results=pd.read_csv("/content/drive/MyDrive/MP_Dataset.csv")
df_results["ICG"]=(df_results["Probs"]>0.5).astype(int)
df_results=df_results.drop_duplicates(subset=['Compound'],keep='first').reset_index(drop=True)
df_results["comp"]=df_results["Compound"].apply(myfunc)
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_results['comp']])
pred_test=model.predict(x_label)
y_label= np.asarray(df_results["ICG"])

In [ ]:
print(classification_report(y_label,pred_test))

              precision    recall  f1-score   support

           0       0.94      0.98      0.96       499
           1       0.44      0.19      0.26        37

    accuracy                           0.93       536
   macro avg       0.69      0.59      0.61       536
weighted avg       0.91      0.93      0.91       536



In [ ]:
# X, y = x_label,y_label
# # print(X.shape, y.shape)
# # create loocv procedure
# cv = LeaveOneOut()
# # create model
# model1 = sklearn.svm.LinearSVC(C=trial.params['C'],random_state=42)
# # evaluate model
# scores = cross_val_score(model1, X, y, scoring='accuracy', cv=cv, n_jobs=-1)
# # report performance
# print('Accuracy: %.3f (STD: %.3f)' % (mean(scores), std(scores)))

DFT DATASET

In [ ]:
df_results=pd.read_csv("/content/drive/MyDrive/final_test.csv")
df_results=df_results[df_results["Table"]>1]
df_results["comp"]=df_results["Compound"].apply(myfunc)
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_results['comp']])
pred_test=model.predict(x_label)
y_label= np.asarray(df_results["ICG"])

In [ ]:
print(classification_report(y_label,pred_test))

              precision    recall  f1-score   support

           0       0.86      1.00      0.92        18
           1       0.00      0.00      0.00         3

    accuracy                           0.86        21
   macro avg       0.43      0.50      0.46        21
weighted avg       0.73      0.86      0.79        21



In [ ]:
# X, y = x_label,y_label
# # print(X.shape, y.shape)
# # create loocv procedure
# cv = LeaveOneOut()
# # create model
# model1 = sklearn.svm.LinearSVC(C=trial.params['C'],random_state=42)
# # evaluate model
# scores = cross_val_score(model1, X, y, scoring='accuracy', cv=cv, n_jobs=-1)
# # report performance
# print('Accuracy: %.3f (STD: %.3f)' % (mean(scores), std(scores)))

In [ ]:
# df_results=pd.read_csv("/content/drive/MyDrive/final_test.csv")
# df_results=df_results[df_results["Table"]<2]
# df_results=df_results.drop_duplicates(subset=['Compound'],keep='first').reset_index(drop=True)
# df_results["comp"]=df_results["Compound"].apply(myfunc)
# x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_results['comp']])
# pred_test=model.predict(x_label)
# y_label= np.asarray(df_results["ICG"])

In [ ]:
# print(classification_report(y_label,pred_test))

In [ ]:
# df_results["preds"]=pred_test
# df_results

LLZO DATASET

In [ ]:
df_results=pd.read_csv("/content/drive/MyDrive/Varun_LLZO-DATA.csv")
df_results["comp"]=df_results["Combined"].apply(myfunc)
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_results['comp']])
pred_test=model.predict(x_label)
y_label= np.asarray(df_results["good_cond"])

In [ ]:
print(classification_report(y_label,pred_test))

              precision    recall  f1-score   support

           0       1.00      0.01      0.02        88
           1       0.50      1.00      0.67        88

    accuracy                           0.51       176
   macro avg       0.75      0.51      0.35       176
weighted avg       0.75      0.51      0.35       176



In [ ]:
# X, y = x_label,y_label
# # print(X.shape, y.shape)
# # create loocv procedure
# cv = LeaveOneOut()
# # create model
# model1 = sklearn.svm.LinearSVC(C=trial.params['C'],random_state=42)
# # evaluate model
# scores = cross_val_score(model1, X, y, scoring='accuracy', cv=cv, n_jobs=-1)
# # report performance
# print('Accuracy: %.3f (STD: %.3f)' % (mean(scores), std(scores)))

LLZO DATASET AT ROOM T

In [ ]:
df_results=pd.read_csv("/content/drive/MyDrive/RoomT.csv")
df_results=df_results[df_results['room_t']>0]
df_results["comp"]=df_results["Combined"].apply(myfunc)
x_label= np.asarray([sum_pool(x, mat2vec_model.dictionary, mat2vec_model.vectors) for x in df_results['comp']])
pred_test=model.predict(x_label)
y_label= np.asarray(df_results["good_cond"])

In [ ]:
print(classification_report(y_label,pred_test))

              precision    recall  f1-score   support

           0       1.00      0.01      0.03        70
           1       0.50      1.00      0.67        70

    accuracy                           0.51       140
   macro avg       0.75      0.51      0.35       140
weighted avg       0.75      0.51      0.35       140



In [ ]:
# X, y = x_label,y_label
# # print(X.shape, y.shape)
# # create loocv procedure
# cv = LeaveOneOut()
# # create model
# model1 = sklearn.svm.LinearSVC(C=trial.params['C'],random_state=42)
# # evaluate model
# scores = cross_val_score(model1, X, y, scoring='accuracy', cv=cv, n_jobs=-1)
# # report performance
# print('Accuracy: %.3f (STD: %.3f)' % (mean(scores), std(scores)))